# 06 Using Surge to make Music

So far we've been poking at surge in a variety of ways. Lets make a chunk of music using it and the
popular 'mido' library.

In [1]:
import sys
sys.path.append( "../../surge/cmake-build-debug-xc" )

import surgepy
import surgepy.constants as srco
import IPython

surgepy.getVersion()

'1.8.more-python.185c1075'

In [2]:
import mido

We are going to use the 4th goldberg variation from "Dave's JS Bach Page" http://www.jsbach.net/midi/ then load it with mido


In [3]:
bachurl = "http://www.jsbach.net/midi/bwv988/988-v04.mid"
import urllib.request
import tempfile

with urllib.request.urlopen(bachurl) as f:
    midiData = f.read()

tmpdir = tempfile.gettempdir()
midiF = tmpdir + "/988-v04.mid"
with open(midiF, "wb") as f:
    f.write( midiData )
  

And so now lets read that midi file and render the note on and offs into 25 seconds or so of audio.

In [4]:
mf = mido.MidiFile( midiF )
currTime = 0
currBlock = 0;
maxTime = 25 # how many seconds of bach do we want

s    = surgepy.createSurge( 44100 )
bps  = s.getSampleRate() / s.getBlockSize() 
buf  = s.createMultiBlock( int( bps * maxTime ) ) 

fd = s.getFactoryDataPath()
pt = fd + "/patches_factory/Polysynths/MG.fxp"
s.loadPatch( pt )

for msg in mf:
    if currTime + msg.time > maxTime:
        break
    if msg.time != 0:
        blocks = round( msg.time * bps );
        s.processMultiBlock( buf, currBlock, blocks )
        currBlock = currBlock + blocks
        currTime = currTime + msg.time
        
    if msg.type == 'note_on' and msg.velocity != 0:
        s.playNote( 0, msg.note, msg.velocity, 0 )
    if msg.type == 'note_off' or (msg.type == 'note_on' and msg.velocity == 0 ):
        s.releaseNote( 0, msg.note, 0 )
        
print( "Done" )
        
IPython.display.Audio( buf, rate=s.getSampleRate() )

Done
